In [1]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt


import mxnet as mx
from gluonts.dataset.pandas import PandasDataset
from gluonts.mx import DeepAREstimator, Trainer
# from gluonts.distribution.neg_binomial import NegativeBinomialOutput
from gluonts.mx.distribution.neg_binomial import NegativeBinomialOutput
from gluonts.mx.trainer.callback import TrainingHistory

from gluonts.dataset.util import to_pandas
from gluonts.dataset.pandas import PandasDataset
from gluonts.evaluation.backtest import make_evaluation_predictions

In [2]:
mx.context.num_gpus()

0

In [3]:
# df = pd.read_csv('Merged-update_hourly.csv')
df = pd.read_csv('../../../data/Merged-update_hourly.csv')
df.fillna(0, inplace=True)

In [4]:
df

Time  WS_S1  WS_S4  FLOW_S25A  GATE_S25A  HWS_S25A  TWS_S25A  \
0        1/1/10 00:00   0.33   0.34        0.0        0.0      2.17      0.49   
1        1/1/10 01:00  -0.29  -0.28        0.0        0.0      2.17      0.02   
2        1/1/10 02:00  -0.81  -0.73        0.0        0.0      2.17     -0.49   
3        1/1/10 03:00  -0.98  -0.85        0.0        0.0      2.15     -0.75   
4        1/1/10 04:00  -0.69  -0.49        0.0        0.0      2.13     -0.55   
...               ...    ...    ...        ...        ...       ...       ...   
96427  12/31/20 19:00   1.24   1.19        0.0        0.0      1.92      1.25   
96428  12/31/20 20:00   1.62   1.61        0.0        0.0      1.92      1.64   
96429  12/31/20 21:00   1.98   1.90        0.0        0.0      1.93      2.00   
96430  12/31/20 22:00   2.13   2.03        0.0        0.0      1.94      2.13   
96431  12/31/20 23:00   1.96   1.81        0.0        0.0      1.96      1.98   

       FLOW_S25B  GATE_S25B  GATE_S25B2  HWS_S25B  TWS_S25B  PUMP_S25B  \
0            0.0        0.0         0.0      2.84      0.58        0.0   
1            0.0        0.0         0.0      2.84     -0.07        0.0   
2            0.0        0.0         0.0      2.84     -0.62        0.0   
3            0.0        0.0         0.0      2.83     -0.82        0.0   
4            0.0        0.0         0.0      2.84     -0.53        0.0   
...          ...        ...         ...       ...       ...        ...   
96427        0.0        0.0         0.0      2.86      1.31        0.0   
96428        0.0        0.0         0.0      2.88      1.68        0.0   
96429        0.0        0.0         0.0      2.89      2.04        0.0   
96430        0.0        0.0         0.0      2.90      2.21        0.0   
96431        0.0        0.0         0.0      2.91      2.06        0.0   

       FLOW_S26  GATE_S26_1  GATE_S26_2  HWS_S26  TWS_S26  PUMP_S26  MEAN_RAIN  
0          0.00         0.0        0.00     2.78    0.505       0.0        0.0  
1          0.00         0.0        0.00     2.78   -0.110       0.0        0.0  
2          0.00         0.0        0.00     2.79   -0.650       0.0        0.0  
3          0.00         0.0        0.00     2.79   -0.850       0.0        0.0  
4          0.00         0.0        0.00     2.79   -0.550       0.0        0.0  
...         ...         ...         ...      ...      ...       ...        ...  
96427    456.34         0.0        2.61     2.49    1.290       0.0        0.0  
96428    380.19         0.0        2.62     2.48    1.660       0.0        0.0  
96429    287.12         0.0        2.62     2.54    2.040       0.0        0.0  
96430    253.27         0.0        2.62     2.58    2.180       0.0        0.0  
96431    294.00         0.0        2.62     2.59    2.050       0.0        0.0  

[96432 rows x 20 columns]

In [5]:
df.loc[:, 'timestamp'] = pd.to_datetime(df.loc[:, 'Time'], infer_datetime_format=True)

In [6]:
df

Time  WS_S1  WS_S4  FLOW_S25A  GATE_S25A  HWS_S25A  TWS_S25A  \
0        1/1/10 00:00   0.33   0.34        0.0        0.0      2.17      0.49   
1        1/1/10 01:00  -0.29  -0.28        0.0        0.0      2.17      0.02   
2        1/1/10 02:00  -0.81  -0.73        0.0        0.0      2.17     -0.49   
3        1/1/10 03:00  -0.98  -0.85        0.0        0.0      2.15     -0.75   
4        1/1/10 04:00  -0.69  -0.49        0.0        0.0      2.13     -0.55   
...               ...    ...    ...        ...        ...       ...       ...   
96427  12/31/20 19:00   1.24   1.19        0.0        0.0      1.92      1.25   
96428  12/31/20 20:00   1.62   1.61        0.0        0.0      1.92      1.64   
96429  12/31/20 21:00   1.98   1.90        0.0        0.0      1.93      2.00   
96430  12/31/20 22:00   2.13   2.03        0.0        0.0      1.94      2.13   
96431  12/31/20 23:00   1.96   1.81        0.0        0.0      1.96      1.98   

       FLOW_S25B  GATE_S25B  GATE_S25B2  ...  TWS_S25B  PUMP_S25B  FLOW_S26  \
0            0.0        0.0         0.0  ...      0.58        0.0      0.00   
1            0.0        0.0         0.0  ...     -0.07        0.0      0.00   
2            0.0        0.0         0.0  ...     -0.62        0.0      0.00   
3            0.0        0.0         0.0  ...     -0.82        0.0      0.00   
4            0.0        0.0         0.0  ...     -0.53        0.0      0.00   
...          ...        ...         ...  ...       ...        ...       ...   
96427        0.0        0.0         0.0  ...      1.31        0.0    456.34   
96428        0.0        0.0         0.0  ...      1.68        0.0    380.19   
96429        0.0        0.0         0.0  ...      2.04        0.0    287.12   
96430        0.0        0.0         0.0  ...      2.21        0.0    253.27   
96431        0.0        0.0         0.0  ...      2.06        0.0    294.00   

       GATE_S26_1  GATE_S26_2  HWS_S26  TWS_S26  PUMP_S26  MEAN_RAIN  \
0             0.0        0.00     2.78    0.505       0.0        0.0   
1             0.0        0.00     2.78   -0.110       0.0        0.0   
2             0.0        0.00     2.79   -0.650       0.0        0.0   
3             0.0        0.00     2.79   -0.850       0.0        0.0   
4             0.0        0.00     2.79   -0.550       0.0        0.0   
...           ...         ...      ...      ...       ...        ...   
96427         0.0        2.61     2.49    1.290       0.0        0.0   
96428         0.0        2.62     2.48    1.660       0.0        0.0   
96429         0.0        2.62     2.54    2.040       0.0        0.0   
96430         0.0        2.62     2.58    2.180       0.0        0.0   
96431         0.0        2.62     2.59    2.050       0.0        0.0   

                timestamp  
0     2010-01-01 00:00:00  
1     2010-01-01 01:00:00  
2     2010-01-01 02:00:00  
3     2010-01-01 03:00:00  
4     2010-01-01 04:00:00  
...                   ...  
96427 2020-12-31 19:00:00  
96428 2020-12-31 20:00:00  
96429 2020-12-31 21:00:00  
96430 2020-12-31 22:00:00  
96431 2020-12-31 23:00:00  

[96432 rows x 21 columns]

In [7]:
df.columns

Index(['Time', 'WS_S1', 'WS_S4', 'FLOW_S25A', 'GATE_S25A', 'HWS_S25A',
       'TWS_S25A', 'FLOW_S25B', 'GATE_S25B', 'GATE_S25B2', 'HWS_S25B',
       'TWS_S25B', 'PUMP_S25B', 'FLOW_S26', 'GATE_S26_1', 'GATE_S26_2',
       'HWS_S26', 'TWS_S26', 'PUMP_S26', 'MEAN_RAIN', 'timestamp'],
      dtype='object')

In [8]:
train_df = df.iloc[:int(len(df)*0.8), :]
test_df = df.iloc[int(len(df)*0.8):, :]

In [9]:
train_df.shape

(77145, 21)

In [10]:
test_df

Time  WS_S1  WS_S4  FLOW_S25A  GATE_S25A  HWS_S25A  TWS_S25A  \
77145  10/20/18 09:00   1.06   1.01        0.0        0.0      2.41      1.07   
77146  10/20/18 10:00   0.68   0.63        0.0        0.0      2.41      0.71   
77147  10/20/18 11:00   0.31   0.32        0.0        0.0      2.41      0.33   
77148  10/20/18 12:00   0.20   0.23        0.0        0.0      2.40      0.24   
77149  10/20/18 13:00   0.41   0.42        0.0        0.0      2.39      0.42   
...               ...    ...    ...        ...        ...       ...       ...   
96427  12/31/20 19:00   1.24   1.19        0.0        0.0      1.92      1.25   
96428  12/31/20 20:00   1.62   1.61        0.0        0.0      1.92      1.64   
96429  12/31/20 21:00   1.98   1.90        0.0        0.0      1.93      2.00   
96430  12/31/20 22:00   2.13   2.03        0.0        0.0      1.94      2.13   
96431  12/31/20 23:00   1.96   1.81        0.0        0.0      1.96      1.98   

       FLOW_S25B  GATE_S25B  GATE_S25B2  ...  TWS_S25B  PUMP_S25B  FLOW_S26  \
77145        0.0        0.0         0.0  ...      1.15        0.0    469.19   
77146        0.0        0.0         0.0  ...      0.82        0.0      0.00   
77147        0.0        0.0         0.0  ...      0.42        0.0      0.00   
77148        0.0        0.0         0.0  ...      0.35        0.0      0.00   
77149        0.0        0.0         0.0  ...      0.48        0.0      0.00   
...          ...        ...         ...  ...       ...        ...       ...   
96427        0.0        0.0         0.0  ...      1.31        0.0    456.34   
96428        0.0        0.0         0.0  ...      1.68        0.0    380.19   
96429        0.0        0.0         0.0  ...      2.04        0.0    287.12   
96430        0.0        0.0         0.0  ...      2.21        0.0    253.27   
96431        0.0        0.0         0.0  ...      2.06        0.0    294.00   

       GATE_S26_1  GATE_S26_2  HWS_S26  TWS_S26  PUMP_S26  MEAN_RAIN  \
77145         0.0        2.61     2.35     1.11       0.0        0.0   
77146         0.0        0.00     2.62     0.72       0.0        0.0   
77147         0.0        0.00     2.62     0.37       0.0        0.0   
77148         0.0        0.00     2.67     0.28       0.0        0.0   
77149         0.0        0.00     2.72     0.45       0.0        0.0   
...           ...         ...      ...      ...       ...        ...   
96427         0.0        2.61     2.49     1.29       0.0        0.0   
96428         0.0        2.62     2.48     1.66       0.0        0.0   
96429         0.0        2.62     2.54     2.04       0.0        0.0   
96430         0.0        2.62     2.58     2.18       0.0        0.0   
96431         0.0        2.62     2.59     2.05       0.0        0.0   

                timestamp  
77145 2018-10-20 09:00:00  
77146 2018-10-20 10:00:00  
77147 2018-10-20 11:00:00  
77148 2018-10-20 12:00:00  
77149 2018-10-20 13:00:00  
...                   ...  
96427 2020-12-31 19:00:00  
96428 2020-12-31 20:00:00  
96429 2020-12-31 21:00:00  
96430 2020-12-31 22:00:00  
96431 2020-12-31 23:00:00  

[19287 rows x 21 columns]

In [11]:
train_ds = PandasDataset(
    train_df,
    target = 'WS_S1',
    timestamp = 'timestamp',
    feat_dynamic_real = ['WS_S4', 'FLOW_S25A', 'GATE_S25A', 'HWS_S25A',
       'TWS_S25A', 'FLOW_S25B', 'GATE_S25B', 'GATE_S25B2', 'HWS_S25B',
       'TWS_S25B', 'PUMP_S25B', 'FLOW_S26', 'GATE_S26_1', 'GATE_S26_2',
       'HWS_S26', 'TWS_S26', 'PUMP_S26', 'MEAN_RAIN',],
    freq = 'H'
)

In [12]:
test_ds = PandasDataset(
    test_df,
    target = 'WS_S1',
    timestamp = 'timestamp',
    feat_dynamic_real = ['WS_S4', 'FLOW_S25A', 'GATE_S25A', 'HWS_S25A',
       'TWS_S25A', 'FLOW_S25B', 'GATE_S25B', 'GATE_S25B2', 'HWS_S25B',
       'TWS_S25B', 'PUMP_S25B', 'FLOW_S26', 'GATE_S26_1', 'GATE_S26_2',
       'HWS_S26', 'TWS_S26', 'PUMP_S26', 'MEAN_RAIN',],
    freq = 'H'
)

#### training

In [54]:
K = 24
n_hours = 24*3

In [56]:
trainer=Trainer(
    learning_rate=1e-3,
    epochs=150,
    num_batches_per_epoch=100,
    add_default_callbacks=True,
    weight_decay=1e-06)

estimator = DeepAREstimator(
    prediction_length=K,
    freq="H",
    distr_output = NegativeBinomialOutput(),
    use_feat_dynamic_real=True,
    num_layers=1, 
    num_cells=64, 
    cell_type='gru',  # lstm or gru. default: lstm
    batch_size=32,
    trainer=trainer,
    dropout_rate=0.4,
    impute_missing_values=True
)

model = estimator.train(train_ds)

  0%|                                                                                               | 0/100 [00:00<?, ?it/s]WARNING:gluonts.trainer:Batch [1] of Epoch[1] gave NaN loss and it will be ignored


 18%|█████████▏                                         | 18/100 [00:59<04:34,  3.35s/it, epoch=3/150, avg_epoch_loss=0.797]WARNING:gluonts.trainer:Batch [19] of Epoch[2] gave NaN loss and it will be ignored


 52%|██████████████████████████▌                        | 52/100 [02:36<02:29,  3.12s/it, epoch=5/150, avg_epoch_loss=0.726]WARNING:gluonts.trainer:Batch [53] of Epoch[4] gave NaN loss and it will be ignored


 81%|██████████████████████████████████████████          | 81/100 [04:08<01:01,  3.21s/it, epoch=7/150, avg_epoch_loss=0.48]WARNING:gluonts.trainer:Batch [82] of Epoch[6] gave NaN loss and it will be ignored


 83%|██████████████████████████████████████████▎        | 83/100 [04:17<00:49,  2.92s/it, epoch=9/150, avg_epoch_loss=0.439]WARNING:gluonts.trainer:Batch [84] of Epoch[8] gave NaN loss and it will be ignored


...

 62%|██████████████████████████████▍                  | 62/100 [03:01<01:46,  2.81s/it, epoch=144/150, avg_epoch_loss=0.178]WARNING:gluonts.trainer:Batch [63] of Epoch[143] gave NaN loss and it will be ignored


 92%|█████████████████████████████████████████████    | 92/100 [04:34<00:24,  3.09s/it, epoch=145/150, avg_epoch_loss=0.148]WARNING:gluonts.trainer:Batch [94] of Epoch[144] gave NaN loss and it will be ignored


 89%|███████████████████████████████████████████▌     | 89/100 [04:21<00:31,  2.84s/it, epoch=147/150, avg_epoch_loss=0.106]WARNING:gluonts.trainer:Batch [93] of Epoch[146] gave NaN loss and it will be ignored


 25%|████████████▎                                    | 25/100 [01:10<03:21,  2.68s/it, epoch=150/150, avg_epoch_loss=0.197]WARNING:gluonts.trainer:Batch [26] of Epoch[149] gave NaN loss and it will be ignored


100%|████████████████████████████████████████████████| 100/100 [04:55<00:00,  2.95s/it, epoch=150/150, avg_epoch_loss=0.152]


#### predicted y

In [43]:
# forecast_it, ts_it = make_evaluation_predictions(dataset=test_ds, predictor=model, num_samples=500)
# forecasts = list(forecast_it)
# tss = list(ts_it)
# evaluator = Evaluator(quantiles=[0.1, 0.5, 0.9])
# agg_metrics, item_metrics = evaluator(tss, forecasts)

In [44]:
quantiles = ['0.025', '0.1', '0.2', '0.3', '0.4', '0.5', '0.6', '0.7', '0.8', '0.9', '0.975']
q50 = 5

In [45]:
test_ds_predict_q50_all = np.array([])

for i in range(len(test_df)-n_hours-K+1):
    print(i)
    
    cut = df.iloc[len(train_df)+i:len(train_df)+i+n_hours+K, :]

    test_ds = PandasDataset(
    cut,
    target = 'WS_S1',
    timestamp = 'timestamp',
    feat_dynamic_real = ['WS_S4', 'FLOW_S25A', 'GATE_S25A', 'HWS_S25A',
       'TWS_S25A', 'FLOW_S25B', 'GATE_S25B', 'GATE_S25B2', 'HWS_S25B',
       'TWS_S25B', 'PUMP_S25B', 'FLOW_S26', 'GATE_S26_1', 'GATE_S26_2',
       'HWS_S26', 'TWS_S26', 'PUMP_S26', 'MEAN_RAIN',],
        freq = 'H'
    )
    
    forecast_it, ts_it = make_evaluation_predictions(dataset=test_ds, predictor=model, num_samples=200)
    test_ds_predict = list(forecast_it)
    test_ds_predict_quantiles = test_ds_predict[0].samples
    test_ds_predict_q50 = test_ds_predict_quantiles.mean(axis=0)
    test_ds_predict_q50_all = np.concatenate((test_ds_predict_q50_all, test_ds_predict_q50), axis=None)
    print(test_ds_predict_q50_all)
    print(test_ds_predict_q50_all.shape)
    print('------')

0
[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125      0.815      1.73000002 2.2750001  2.93499994 2.25500011]
(24,)
------
1
[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125      0.815      1.73000002 2.2750001  2.93499994 2.25500011
 1.86000001 1.65499997 1.15499997 0.52999997 0.14       0.41
 1.08500004 1.97500002 2.28500009 2.50999999 2.58500004 2.33500004
 2.13000011 1.35000002 0.90499997 0.235      0.055      0.155
 0.745      1.59000003 2.47000003 2.65499997 2.28999996 2.29999995]
(48,)
------
2
[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125  

[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125      0.815      1.73000002 2.2750001  2.93499994 2.25500011
 1.86000001 1.65499997 1.15499997 0.52999997 0.14       0.41
 1.08500004 1.97500002 2.28500009 2.50999999 2.58500004 2.33500004
 2.13000011 1.35000002 0.90499997 0.235      0.055      0.155
 0.745      1.59000003 2.47000003 2.65499997 2.28999996 2.29999995
 1.59000003 1.19500005 0.63999999 0.145      0.495      1.125
 1.93499994 2.22000003 2.38499999 2.5        2.32500005 2.125
 1.44500005 0.98000002 0.285      0.055      0.08       0.70999998
 1.69500005 2.57999992 2.53500009 2.34500003 2.42000008 2.1099999
 1.         0.5        0.12       0.43000001 1.09500003 1.87
 2.16499996 2.4749999  2.32500005 2.24499989 2.19000006 1.47000003
 0.89999998 0.22       0.03       0.16       0.77499998 1.72000003
 2.2750001  2.7249999  2.41499996 2

[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125      0.815      1.73000002 2.2750001  2.93499994 2.25500011
 1.86000001 1.65499997 1.15499997 0.52999997 0.14       0.41
 1.08500004 1.97500002 2.28500009 2.50999999 2.58500004 2.33500004
 2.13000011 1.35000002 0.90499997 0.235      0.055      0.155
 0.745      1.59000003 2.47000003 2.65499997 2.28999996 2.29999995
 1.59000003 1.19500005 0.63999999 0.145      0.495      1.125
 1.93499994 2.22000003 2.38499999 2.5        2.32500005 2.125
 1.44500005 0.98000002 0.285      0.055      0.08       0.70999998
 1.69500005 2.57999992 2.53500009 2.34500003 2.42000008 2.1099999
 1.         0.5        0.12       0.43000001 1.09500003 1.87
 2.16499996 2.4749999  2.32500005 2.24499989 2.19000006 1.47000003
 0.89999998 0.22       0.03       0.16       0.77499998 1.72000003
 2.2750001  2.7249999  2.41499996 2

[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125      0.815      1.73000002 2.2750001  2.93499994 2.25500011
 1.86000001 1.65499997 1.15499997 0.52999997 0.14       0.41
 1.08500004 1.97500002 2.28500009 2.50999999 2.58500004 2.33500004
 2.13000011 1.35000002 0.90499997 0.235      0.055      0.155
 0.745      1.59000003 2.47000003 2.65499997 2.28999996 2.29999995
 1.59000003 1.19500005 0.63999999 0.145      0.495      1.125
 1.93499994 2.22000003 2.38499999 2.5        2.32500005 2.125
 1.44500005 0.98000002 0.285      0.055      0.08       0.70999998
 1.69500005 2.57999992 2.53500009 2.34500003 2.42000008 2.1099999
 1.         0.5        0.12       0.43000001 1.09500003 1.87
 2.16499996 2.4749999  2.32500005 2.24499989 2.19000006 1.47000003
 0.89999998 0.22       0.03       0.16       0.77499998 1.72000003
 2.2750001  2.7249999  2.41499996 2

[2.14499998 1.68499994 1.34500003 0.97000003 0.43000001 0.11
 0.38999999 1.245      1.91499996 2.2349999  2.36500001 2.24000001
 2.29500008 1.90999997 1.48000002 0.79500002 0.25999999 0.06
 0.125      0.815      1.73000002 2.2750001  2.93499994 2.25500011
 1.86000001 1.65499997 1.15499997 0.52999997 0.14       0.41
 1.08500004 1.97500002 2.28500009 2.50999999 2.58500004 2.33500004
 2.13000011 1.35000002 0.90499997 0.235      0.055      0.155
 0.745      1.59000003 2.47000003 2.65499997 2.28999996 2.29999995
 1.59000003 1.19500005 0.63999999 0.145      0.495      1.125
 1.93499994 2.22000003 2.38499999 2.5        2.32500005 2.125
 1.44500005 0.98000002 0.285      0.055      0.08       0.70999998
 1.69500005 2.57999992 2.53500009 2.34500003 2.42000008 2.1099999
 1.         0.5        0.12       0.43000001 1.09500003 1.87
 2.16499996 2.4749999  2.32500005 2.24499989 2.19000006 1.47000003
 0.89999998 0.22       0.03       0.16       0.77499998 1.72000003
 2.2750001  2.7249999  2.41499996 2

...

[2.14499998 1.68499994 1.34500003 ... 1.34500003 1.78499997 2.        ]
(451920,)
------
18830
[2.14499998 1.68499994 1.34500003 ... 1.99000001 1.88999999 2.47000003]
(451944,)
------
18831
[2.14499998 1.68499994 1.34500003 ... 2.14499998 2.33500004 2.5       ]
(451968,)
------
18832
[2.14499998 1.68499994 1.34500003 ... 2.29500008 2.2249999  2.23000002]
(451992,)
------
18833
[2.14499998 1.68499994 1.34500003 ... 2.4000001  2.00999999 1.60000002]
(452016,)
------
18834
[2.14499998 1.68499994 1.34500003 ... 2.06500006 1.45500004 0.97500002]
(452040,)
------
18835
[2.14499998 1.68499994 1.34500003 ... 1.67999995 0.91000003 0.11      ]
(452064,)
------
18836
[2.14499998 1.68499994 1.34500003 ... 0.85000002 0.11       0.        ]
(452088,)
------
18837
[2.14499998 1.68499994 1.34500003 ... 0.1        0.         0.        ]
(452112,)
------
18838
[2.14499998 1.68499994 1.34500003 ... 0.         0.         0.        ]
(452136,)
------
18839
[2.14499998 1.68499994 1.34500003 ... 0.         0

[2.14499998 1.68499994 1.34500003 ... 1.25       1.68499994 1.94500005]
(454008,)
------
18917
[2.14499998 1.68499994 1.34500003 ... 1.80499995 2.04500008 2.2249999 ]
(454032,)
------
18918
[2.14499998 1.68499994 1.34500003 ... 2.06999993 2.31500006 2.26999998]
(454056,)
------
18919
[2.14499998 1.68499994 1.34500003 ... 2.41000009 2.43499994 1.97500002]
(454080,)
------
18920
[2.14499998 1.68499994 1.34500003 ... 2.40499997 2.1099999  1.43499994]
(454104,)
------
18921
[2.14499998 1.68499994 1.34500003 ... 2.08500004 1.47500002 1.03999996]
(454128,)
------
18922
[2.14499998 1.68499994 1.34500003 ... 1.61500001 1.05999994 0.745     ]
(454152,)
------
18923
[2.14499998 1.68499994 1.34500003 ... 1.12       0.73000002 0.285     ]
(454176,)
------
18924
[2.14499998 1.68499994 1.34500003 ... 0.70999998 0.465      0.30000001]
(454200,)
------
18925
[2.14499998 1.68499994 1.34500003 ... 0.35499999 0.39500001 0.69      ]
(454224,)
------
18926
[2.14499998 1.68499994 1.34500003 ... 0.31       0

[2.14499998 1.68499994 1.34500003 ... 1.63499999 1.43499994 1.69000006]
(456096,)
------
19004
[2.14499998 1.68499994 1.34500003 ... 1.57500005 1.67499995 1.82500005]
(456120,)
------
19005
[2.14499998 1.68499994 1.34500003 ... 1.93499994 2.11999989 2.16000009]
(456144,)
------
19006
[2.14499998 1.68499994 1.34500003 ... 2.14499998 2.00500011 2.125     ]
(456168,)
------
19007
[2.14499998 1.68499994 1.34500003 ... 2.25       2.1500001  1.71500003]
(456192,)
------
19008
[2.14499998 1.68499994 1.34500003 ... 1.98500001 1.71000004 1.21000004]
(456216,)
------
19009
[2.14499998 1.68499994 1.34500003 ... 1.75       1.21500003 1.04499996]
(456240,)
------
19010
[2.14499998 1.68499994 1.34500003 ... 1.28499997 1.16999996 0.86500001]
(456264,)
------
19011
[2.14499998 1.68499994 1.34500003 ... 1.10000002 0.91000003 0.83499998]
(456288,)
------
19012
[2.14499998 1.68499994 1.34500003 ... 0.96499997 0.87       0.97500002]
(456312,)
------
19013
[2.14499998 1.68499994 1.34500003 ... 0.93000001 1

[2.14499998 1.68499994 1.34500003 ... 1.08500004 1.12       1.32500005]
(458184,)
------
19091
[2.14499998 1.68499994 1.34500003 ... 1.19500005 1.25999999 1.57500005]
(458208,)
------
19092
[2.14499998 1.68499994 1.34500003 ... 1.31500006 1.41499996 1.44500005]
(458232,)
------
19093
[2.14499998 1.68499994 1.34500003 ... 1.53499997 1.40999997 0.995     ]
(458256,)
------
19094
[2.14499998 1.68499994 1.34500003 ... 1.27999997 1.16499996 0.80000001]
(458280,)
------
19095
[2.14499998 1.68499994 1.34500003 ... 1.15999997 0.79500002 0.375     ]
(458304,)
------
19096
[2.14499998 1.68499994 1.34500003 ... 0.745      0.29499999 0.01      ]
(458328,)
------
19097
[2.14499998 1.68499994 1.34500003 ... 0.405      0.015      0.        ]
(458352,)
------
19098
[2.14499998 1.68499994 1.34500003 ... 0.         0.         0.        ]
(458376,)
------
19099
[2.14499998 1.68499994 1.34500003 ... 0.         0.         0.125     ]
(458400,)
------
19100
[2.14499998 1.68499994 1.34500003 ... 0.005      0

[2.14499998 1.68499994 1.34500003 ... 1.74000001 1.45500004 1.77499998]
(460272,)
------
19178
[2.14499998 1.68499994 1.34500003 ... 1.74000001 1.67499995 1.92999995]
(460296,)
------
19179
[2.14499998 1.68499994 1.34500003 ... 1.875      1.86500001 1.66499996]
(460320,)
------
19180
[2.14499998 1.68499994 1.34500003 ... 1.83000004 1.86000001 1.52999997]
(460344,)
------
19181
[2.14499998 1.68499994 1.34500003 ... 1.82500005 1.43499994 0.92500001]
(460368,)
------
19182
[2.14499998 1.68499994 1.34500003 ... 1.375      0.94999999 0.60500002]
(460392,)
------
19183
[2.14499998 1.68499994 1.34500003 ... 1.02499998 0.625      0.02      ]
(460416,)
------
19184
[2.14499998 1.68499994 1.34500003 ... 0.685      0.035      0.        ]
(460440,)
------
19185
[2.14499998 1.68499994 1.34500003 ... 0.03       0.         0.045     ]
(460464,)
------
19186
[2.14499998 1.68499994 1.34500003 ... 0.005      0.06       0.59500003]
(460488,)
------
19187
[2.14499998 1.68499994 1.34500003 ... 0.03       0

In [46]:
test_ds_predict_q50_supervised = test_ds_predict_q50_all.reshape((-1, K))
test_ds_predict_q50_supervised.shape

(19192, 24)

In [47]:
test_ds_predict_q50_supervised[0:5]

array([[2.14499998, 1.68499994, 1.34500003, 0.97000003, 0.43000001,
        0.11      , 0.38999999, 1.245     , 1.91499996, 2.2349999 ,
        2.36500001, 2.24000001, 2.29500008, 1.90999997, 1.48000002,
        0.79500002, 0.25999999, 0.06      , 0.125     , 0.815     ,
        1.73000002, 2.2750001 , 2.93499994, 2.25500011],
       [1.86000001, 1.65499997, 1.15499997, 0.52999997, 0.14      ,
        0.41      , 1.08500004, 1.97500002, 2.28500009, 2.50999999,
        2.58500004, 2.33500004, 2.13000011, 1.35000002, 0.90499997,
        0.235     , 0.055     , 0.155     , 0.745     , 1.59000003,
        2.47000003, 2.65499997, 2.28999996, 2.29999995],
       [1.59000003, 1.19500005, 0.63999999, 0.145     , 0.495     ,
        1.125     , 1.93499994, 2.22000003, 2.38499999, 2.5       ,
        2.32500005, 2.125     , 1.44500005, 0.98000002, 0.285     ,
        0.055     , 0.08      , 0.70999998, 1.69500005, 2.57999992,
        2.53500009, 2.34500003, 2.42000008, 2.1099999 ],
       [1.   

#### actual y

In [65]:
from helper import series_to_supervised, stage_series_to_supervised

In [66]:
test_df_supervised = series_to_supervised(test_df[['WS_S1']], n_hours, K)

In [67]:
test_df_supervised.iloc[:, -K:].shape

(19192, 24)

In [68]:
test_df_supervised_y = test_df_supervised.iloc[:, -K:]

In [69]:
test_df_supervised_y

var1(t)  var1(t+1)  var1(t+2)  var1(t+3)  var1(t+4)  var1(t+5)  \
77217     2.53       1.92       1.43       0.92       0.50       0.20   
77218     1.92       1.43       0.92       0.50       0.20       0.47   
77219     1.43       0.92       0.50       0.20       0.47       0.98   
77220     0.92       0.50       0.20       0.47       0.98       1.62   
77221     0.50       0.20       0.47       0.98       1.62       2.12   
...        ...        ...        ...        ...        ...        ...   
96404     1.93       2.19       2.11       1.65       1.24       0.76   
96405     2.19       2.11       1.65       1.24       0.76       0.15   
96406     2.11       1.65       1.24       0.76       0.15      -0.13   
96407     1.65       1.24       0.76       0.15      -0.13      -0.16   
96408     1.24       0.76       0.15      -0.13      -0.16       0.13   

       var1(t+6)  var1(t+7)  var1(t+8)  var1(t+9)  ...  var1(t+14)  \
77217       0.47       0.98       1.62       2.12  ...        1.46   
77218       0.98       1.62       2.12       2.53  ...        0.93   
77219       1.62       2.12       2.53       2.75  ...        0.38   
77220       2.12       2.53       2.75       2.59  ...        0.08   
77221       2.53       2.75       2.59       2.05  ...        0.22   
...          ...        ...        ...        ...  ...         ...   
96404       0.15      -0.13      -0.16       0.13  ...        2.36   
96405      -0.13      -0.16       0.13       0.79  ...        2.18   
96406      -0.16       0.13       0.79       1.34  ...        1.69   
96407       0.13       0.79       1.34       1.80  ...        1.14   
96408       0.79       1.34       1.80       2.19  ...        0.64   

       var1(t+15)  var1(t+16)  var1(t+17)  var1(t+18)  var1(t+19)  var1(t+20)  \
77217        0.93        0.38        0.08        0.22        0.65        1.35   
77218        0.38        0.08        0.22        0.65        1.35        1.90   
77219        0.08        0.22        0.65        1.35        1.90        2.43   
77220        0.22        0.65        1.35        1.90        2.43        2.72   
77221        0.65        1.35        1.90        2.43        2.72        2.76   
...           ...         ...         ...         ...         ...         ...   
96404        2.18        1.69        1.14        0.64        0.11        0.04   
96405        1.69        1.14        0.64        0.11        0.04        0.18   
96406        1.14        0.64        0.11        0.04        0.18        0.77   
96407        0.64        0.11        0.04        0.18        0.77        1.24   
96408        0.11        0.04        0.18        0.77        1.24        1.62   

       var1(t+21)  var1(t+22)  var1(t+23)  
77217        1.90        2.43        2.72  
77218        2.43        2.72        2.76  
77219        2.72        2.76        2.37  
77220        2.76        2.37        1.73  
77221        2.37        1.73        1.23  
...           ...         ...         ...  
96404        0.18        0.77        1.24  
96405        0.77        1.24        1.62  
96406        1.24        1.62        1.98  
96407        1.62        1.98        2.13  
96408        1.98        2.13        1.96  

[19192 rows x 24 columns]

#### performance on test set

In [70]:
from sklearn.metrics import mean_squared_error as mse
from sklearn.metrics import mean_absolute_error as mae


print('MAE = {}'.format(float("{:.3f}".format(mae(test_ds_predict_q50_supervised, test_df_supervised_y)))))
print('RMSE = {}'.format(float("{:.3f}".format(np.sqrt(mse(test_ds_predict_q50_supervised, test_df_supervised_y))))))

MAE = 0.195
RMSE = 0.23
